# Build and install the package

First patch `pyo3-polars`:

- Use [this diff](https://github.com/pola-rs/pyo3-polars/compare/main...Magnus167:pyo3-polars:main) to make changes to the `pyo3-polars` package.

Install the package:

```bash
python -m venv .venv

# source .venv/bin/activate
./.venv/Scripts/activate

pip install maturin ipywidgets

maturin develop --release
```


### Import Python packages


In [1]:
import macrosynergy
import pandas as pd
import numpy as np
import polars as pl
import os

### Import Python bindings - `msyrs`


In [2]:
import msyrs

In [3]:
# DATA_FOLDER_PATH = "E:/Work/jpmaqs-data"
DATA_FOLDER_PATH = "C:/Users/PalashTyagi/Code/go-dataquery/jpmaqs-data"
DQ_CLIENT_ID = os.getenv("DQ_CLIENT_ID")
DQ_CLIENT_SECRET = os.getenv("DQ_CLIENT_SECRET")

In [4]:
import time

nb_start_time = time.time()

In [5]:
dfpath = f"{DATA_FOLDER_PATH}/data/ADPEMPL_SA_P1M1ML1/USD_ADPEMPL_SA_P1M1ML1.csv"

starttime = time.time()
ldf: pl.DataFrame = msyrs.qdf.load_qdf(dfpath)
print(f"Time taken to load qdf: {time.time() - starttime}")
ldf.head(5)

Time taken to load qdf: 0.007575511932373047


shape: (5, 7)
┌────────────┬─────┬────────────────────┬───────────┬─────────┬─────────┬─────────┐
│ real_date  ┆ cid ┆ xcat               ┆ value     ┆ grading ┆ eop_lag ┆ mop_lag │
│ ---        ┆ --- ┆ ---                ┆ ---       ┆ ---     ┆ ---     ┆ ---     │
│ date       ┆ str ┆ str                ┆ f64       ┆ f64     ┆ i64     ┆ i64     │
╞════════════╪═════╪════════════════════╪═══════════╪═════════╪═════════╪═════════╡
│ 2010-03-03 ┆ USD ┆ ADPEMPL_SA_P1M1ML1 ┆ -0.173806 ┆ 3.0     ┆ 3       ┆ 33      │
│ 2010-03-04 ┆ USD ┆ ADPEMPL_SA_P1M1ML1 ┆ -0.173806 ┆ 3.0     ┆ 4       ┆ 34      │
│ 2010-03-05 ┆ USD ┆ ADPEMPL_SA_P1M1ML1 ┆ -0.173806 ┆ 3.0     ┆ 5       ┆ 35      │
│ 2010-03-08 ┆ USD ┆ ADPEMPL_SA_P1M1ML1 ┆ -0.173806 ┆ 3.0     ┆ 8       ┆ 38      │
│ 2010-03-09 ┆ USD ┆ ADPEMPL_SA_P1M1ML1 ┆ -0.173806 ┆ 3.0     ┆ 9       ┆ 39      │
└────────────┴─────┴────────────────────┴───────────┴─────────┴─────────┴─────────┘

In [6]:
cids_dm = "AUD.CAD.CHF.EUR.GBP.JPY.NOK.NZD.SEK.USD".split(".")
cids_em = "CLP.COP.CZK.HUF.IDR.ILS.INR.KRW.MXN.PLN.THB.TRY.TWD.ZAR".split(".")
cids = cids_dm + cids_em
cids_dux = list(set(cids) - set(["IDR", "NZD"]))
ecos = "CPIC_SA_P1M1ML12.CPIC_SJA_P3M3ML3AR.CPIC_SJA_P6M6ML6AR.CPIH_SA_P1M1ML12.CPIH_SJA_P3M3ML3AR.CPIH_SJA_P6M6ML6AR.INFTEFF_NSA.INTRGDP_NSA_P1M1ML12_3MMA.INTRGDPv5Y_NSA_P1M1ML12_3MMA.PCREDITGDP_SJA_D1M1ML12.RGDP_SA_P1Q1QL4_20QMA.RYLDIRS02Y_NSA.RYLDIRS05Y_NSA.PCREDITBN_SJA_P1M1ML12".split(
    "."
)


mkts = "DU02YXR_NSA.DU05YXR_NSA.DU02YXR_VT10.DU05YXR_VT10.EQXR_NSA.EQXR_VT10.FXXR_NSA.FXXR_VT10.FXCRR_NSA.FXTARGETED_NSA.FXUNTRADABLE_NSA".split(
    "."
)
xcats = ecos + mkts

tickers = [f"{c}_{x}" for c in cids for x in xcats]

In [7]:
# downloaded_df: pl.DataFrame = msyrs.download.download_jpmaqs_indicators_as_df(
#     client_id=DQ_CLIENT_ID,
#     client_secret=DQ_CLIENT_SECRET,
#     tickers=tickers,
# )
# downloaded_df.head(5)

In [8]:
pddf = macrosynergy.download.JPMaQSDownload().download(
    tickers=tickers,
    get_catalogue=True,
    show_progress=True,
    start_date="1990-01-01",
)
pddf = macrosynergy.management.types.QuantamentalDataFrame(pddf)

Downloaded JPMAQS catalogue with 18711 tickers.
Removed 21/600 expressions that are not in the JPMaQS catalogue.
Timestamp UTC:  2024-11-22 17:13:07
Connection successful!


Requesting data: 100%|██████████| 29/29 [00:05<00:00,  4.91it/s]


Some dates are missing from the downloaded data. 
2 out of 9107 dates are missing.


In [9]:
starttime = time.time()

big_df: pl.DataFrame = msyrs.qdf.load_qdf_from_download_bank(

    folder_path=DATA_FOLDER_PATH,
    xcats=xcats,

    # folder_path=DATA_FOLDER_PATH, cids=cids

)
print(f"Time taken to load qdf batch: {time.time() - starttime}")


big_df.head(5)

Time taken to load qdf batch: 1.8986454010009766


shape: (5, 7)
┌────────────┬─────┬──────────────────┬──────────┬─────────┬─────────┬─────────┐
│ real_date  ┆ cid ┆ xcat             ┆ value    ┆ grading ┆ eop_lag ┆ mop_lag │
│ ---        ┆ --- ┆ ---              ┆ ---      ┆ ---     ┆ ---     ┆ ---     │
│ date       ┆ str ┆ str              ┆ f64      ┆ f64     ┆ i64     ┆ i64     │
╞════════════╪═════╪══════════════════╪══════════╪═════════╪═════════╪═════════╡
│ 1990-04-26 ┆ AUD ┆ CPIC_SA_P1M1ML12 ┆ 6.434599 ┆ 2.0     ┆ 26      ┆ 223     │
│ 1990-04-27 ┆ AUD ┆ CPIC_SA_P1M1ML12 ┆ 6.434599 ┆ 2.0     ┆ 27      ┆ 224     │
│ 1990-04-30 ┆ AUD ┆ CPIC_SA_P1M1ML12 ┆ 6.434599 ┆ 2.0     ┆ 30      ┆ 227     │
│ 1990-05-01 ┆ AUD ┆ CPIC_SA_P1M1ML12 ┆ 6.434599 ┆ 2.0     ┆ 31      ┆ 228     │
│ 1990-05-02 ┆ AUD ┆ CPIC_SA_P1M1ML12 ┆ 6.434599 ┆ 2.0     ┆ 32      ┆ 229     │
└────────────┴─────┴──────────────────┴──────────┴─────────┴─────────┴─────────┘

In [10]:
big_df.estimated_size("mb")

275.89989376068115

In [11]:
big_df.to_pandas().memory_usage(deep=True).sum() / 1024**2

871.0723962783813

In [12]:
macrosynergy.management.types.QuantamentalDataFrame(big_df.to_pandas()).memory_usage(
    deep=True
).sum() / 1024**2

211.8466453552246

In [13]:
sel_cids = ["USD", "EUR", "GBP", "AUD", "CAD"]
start = "1999-11-14"

In [14]:
starttime = time.time()
eq_df = msyrs.qdf.reduce_dataframe(
    df=big_df,
    cids=sel_cids,
    xcats=["EQXR_NSA", "EQXR_VT10"],

    start=start,
)
print(f"Time taken to reduce qdf: {time.time() - starttime}")
eq_df

Time taken to reduce qdf: 0.34674978256225586


shape: (62_363, 7)
┌────────────┬─────┬───────────┬───────────┬─────────┬─────────┬─────────┐
│ real_date  ┆ cid ┆ xcat      ┆ value     ┆ grading ┆ eop_lag ┆ mop_lag │
│ ---        ┆ --- ┆ ---       ┆ ---       ┆ ---     ┆ ---     ┆ ---     │
│ date       ┆ str ┆ str       ┆ f64       ┆ f64     ┆ i64     ┆ i64     │
╞════════════╪═════╪═══════════╪═══════════╪═════════╪═════════╪═════════╡
│ 2000-05-04 ┆ AUD ┆ EQXR_NSA  ┆ -1.251605 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-05 ┆ AUD ┆ EQXR_NSA  ┆ 1.787455  ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-08 ┆ AUD ┆ EQXR_NSA  ┆ -0.574713 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-09 ┆ AUD ┆ EQXR_NSA  ┆ -0.931278 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-10 ┆ AUD ┆ EQXR_NSA  ┆ -1.523501 ┆ 1.0     ┆ 0       ┆ 0       │
│ …          ┆ …   ┆ …         ┆ …         ┆ …       ┆ …       ┆ …       │
│ 2024-11-15 ┆ USD ┆ EQXR_VT10 ┆ -1.198544 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-18 ┆ USD ┆ EQXR_VT10 ┆ 0.349312  ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-19 ┆ USD ┆ EQXR_VT10 ┆ 0.2776    ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-20 ┆ USD ┆ EQXR_VT10 ┆ -0.014759 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-21 ┆ USD ┆ EQXR_VT10 ┆ 0.483426  ┆ 1.0     ┆ 0       ┆ 0       │
└────────────┴─────┴───────────┴───────────┴─────────┴─────────┴─────────┘

In [15]:
starttime = time.time()
eq_pd_df = pddf.reduce_df(cids=sel_cids, xcats=["EQXR_NSA", "EQXR_VT10"], start=start)
print(f"Time taken to reduce qdf: {time.time() - starttime}")

Time taken to reduce qdf: 0.13223624229431152


In [16]:
fx_xcats = [xc for xc in xcats if xc.startswith("FX")]
starttime = time.time()

fx_df = msyrs.qdf.reduce_dataframe(
    df=big_df, cids=sel_cids, start=start, xcats=fx_xcats, intersect=True
)
print(f"Time taken to reduce qdf: {time.time() - starttime}")

Time taken to reduce qdf: 0.3902719020843506


In [17]:
starttime = time.time()
fx_pd_df = pddf.reduce_df(cids=sel_cids, xcats=fx_xcats, start=start, intersect=True)
print(f"Time taken to reduce qdf: {time.time() - starttime}")

Time taken to reduce qdf: 0.171736478805542


In [18]:
starttime = time.time()
new_df: pl.DataFrame = msyrs.qdf.update_dataframe(df=eq_df, df_add=fx_df)
print("Time taken: ", time.time() - starttime)
new_df.head(10)

Time taken:  0.024325132369995117


shape: (10, 7)
┌────────────┬─────┬──────────┬───────────┬─────────┬─────────┬─────────┐
│ real_date  ┆ cid ┆ xcat     ┆ value     ┆ grading ┆ eop_lag ┆ mop_lag │
│ ---        ┆ --- ┆ ---      ┆ ---       ┆ ---     ┆ ---     ┆ ---     │
│ date       ┆ str ┆ str      ┆ f64       ┆ f64     ┆ i64     ┆ i64     │
╞════════════╪═════╪══════════╪═══════════╪═════════╪═════════╪═════════╡
│ 2000-05-04 ┆ AUD ┆ EQXR_NSA ┆ -1.251605 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-05 ┆ AUD ┆ EQXR_NSA ┆ 1.787455  ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-08 ┆ AUD ┆ EQXR_NSA ┆ -0.574713 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-09 ┆ AUD ┆ EQXR_NSA ┆ -0.931278 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-10 ┆ AUD ┆ EQXR_NSA ┆ -1.523501 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-11 ┆ AUD ┆ EQXR_NSA ┆ -1.579987 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-12 ┆ AUD ┆ EQXR_NSA ┆ 1.80602   ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-15 ┆ AUD ┆ EQXR_NSA ┆ 0.295664  ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-16 ┆ AUD ┆ EQXR_NSA ┆ 1.310187  ┆ 1.0     ┆ 0       ┆ 0       │
│ 2000-05-17 ┆ AUD ┆ EQXR_NSA ┆ -0.711284 ┆ 1.0     ┆ 0       ┆ 0       │
└────────────┴─────┴──────────┴───────────┴─────────┴─────────┴─────────┘

In [19]:
starttime = time.time()
new_pd_df = pddf.update_df(df_add=eq_pd_df,)
print("Time taken: ", time.time() - starttime)

Time taken:  0.8326597213745117


In [20]:
new_df.tail(10)

shape: (10, 7)
┌────────────┬─────┬───────────┬───────────┬─────────┬─────────┬─────────┐
│ real_date  ┆ cid ┆ xcat      ┆ value     ┆ grading ┆ eop_lag ┆ mop_lag │
│ ---        ┆ --- ┆ ---       ┆ ---       ┆ ---     ┆ ---     ┆ ---     │
│ date       ┆ str ┆ str       ┆ f64       ┆ f64     ┆ i64     ┆ i64     │
╞════════════╪═════╪═══════════╪═══════════╪═════════╪═════════╪═════════╡
│ 2024-11-07 ┆ GBP ┆ FXXR_VT10 ┆ 0.806682  ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-08 ┆ GBP ┆ FXXR_VT10 ┆ -0.247346 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-12 ┆ GBP ┆ FXXR_VT10 ┆ -1.083137 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-13 ┆ GBP ┆ FXXR_VT10 ┆ -0.328958 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-14 ┆ GBP ┆ FXXR_VT10 ┆ -0.110526 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-15 ┆ GBP ┆ FXXR_VT10 ┆ -0.700977 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-18 ┆ GBP ┆ FXXR_VT10 ┆ -0.140805 ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-19 ┆ GBP ┆ FXXR_VT10 ┆ 0.223372  ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-20 ┆ GBP ┆ FXXR_VT10 ┆ 0.361783  ┆ 1.0     ┆ 0       ┆ 0       │
│ 2024-11-21 ┆ GBP ┆ FXXR_VT10 ┆ -0.375365 ┆ 1.0     ┆ 0       ┆ 0       │
└────────────┴─────┴───────────┴───────────┴─────────┴─────────┴─────────┘

In [21]:
# df: polars::prelude::DataFrame,
# xcat: String,
# cids: Option<Vec<String>>,
# lback_periods: Option<usize>,
# lback_method: Option<String>,
# half_life: Option<f64>,
# start: Option<String>,
# end: Option<String>,
# est_freq: Option<String>,
# remove_zeros: Option<bool>,
# postfix: Option<String>,
# nan_tolerance: Option<f64>,

starttime = time.time()
hv = msyrs.panel.historic_vol(
    df=new_df,
    xcat="EQXR_NSA",
    cids=None,
    lback_periods=252,
    lback_method="calendar",
    half_life=None,
    start=None,
    end=None,
    est_freq=None,
    remove_zeros=None,
    postfix="_HV",
    nan_tolerance=None,
)
print(f"Time taken: {time.time() - starttime}")

starttime = time.time()
a = 1 + 5
print("Time taken: ", time.time() - starttime)

Time taken: 0.0014519691467285156
Time taken:  0.0


In [22]:
starttime = time.time()
msyrs.qdf.pivot_dataframe_by_ticker(df=new_df).head(10)
print("Time taken: ", time.time() - starttime)

Time taken:  0.054981231689453125


In [23]:
new_pd_df = macrosynergy.management.types.QuantamentalDataFrame(new_pd_df)

In [24]:
starttime = time.time()
new_pd_df.to_wide()
print("Time taken: ", time.time() - starttime)

Time taken:  2.785749673843384


In [25]:
end_time = time.time()
print(f"Time taken: {end_time - nb_start_time} seconds")

Time taken: 58.54259753227234 seconds
